In [1]:
!pip install praat-parselmouth
# !pip install torch==1.11.0

In [2]:
%load_ext autoreload
%autoreload 2

In [ ]:
%pip install Gitpython

### Init auxiliary functions

In [3]:
from mel_extraction import AudioFeaturesParams, mel_spectrogram
from f0_utils import get_lf0_from_wav
import torch
import librosa
from IPython.display import Audio, display


def _load_and_preprocess_audio(audio_file: str, sr) -> torch.Tensor:
        audio, _ = librosa.load(audio_file, sr=sr)

        audio = torch.FloatTensor(audio).squeeze()
        audio /= torch.abs(audio).max()
        audio = audio.unsqueeze(0)
        return audio

/tmp/ipykernel_44387/2238026304.py:3: DeprecationWarning: Please use `map_coordinates` from the `scipy.ndimage` namespace, the `scipy.ndimage.interpolation` namespace is deprecated.
  from scipy.ndimage.interpolation import map_coordinates


### Initialize model

In [ ]:
device="cuda:0"
model_jit_path = "/mnt/data1/home/ext.akashkin/voice-conversion/model.pt"

In [ ]:
params = AudioFeaturesParams()

traced = torch.jit.load(model_jit_path)

: 

### Prepare audio paths

In [11]:
wav_x_path = '/mnt/data1/home/ext.akashkin/voice-conversion/inference/wavs/misha1.wav'
wav_target_path = '/mnt/data1/home/ext.akashkin/voice-conversion/data/vctk-trimmed-dataset-mic1/data/p230/p230_003_mic1.wav'

### Convert audio

In [ ]:

wav_source = _load_and_preprocess_audio(wav_x_path, 16000).to(device)

wav_ref = _load_and_preprocess_audio(wav_target_path, 24000)
mel_ref = mel_spectrogram(wav_ref, params).to(device)

pitch = get_lf0_from_wav(wav_x_path)
pitch = pitch.to(device).float()

In [ ]:

y = traced(wav_source, mel_ref, pitch)

print("Source sentence")
display(Audio(wav_x_path))

print("Target Voice")
display(Audio(wav_target_path))

print("Converted")
display(Audio(y.cpu().squeeze().detach().numpy(), rate=24000))

In [87]:
!ls /mnt/data1/home/ext.akashkin/voice-conversion/data/vctk-trimmed-dataset-mic1/data/p226/p226_003_mic1.wav

/mnt/data1/home/ext.akashkin/voice-conversion/data/vctk-trimmed-dataset-mic1/data/p226/p226_003_mic1.wav


In [88]:
pitch.shape, wav_source.shape, mel_ref.shape

(torch.Size([1, 2, 2967]), torch.Size([1, 475200]), torch.Size([1, 80, 660]))

In [11]:
!ls /mnt/data1/home/ext.akashkin/voice-conversion/inference/wavs

 SING1.wav	  dinara_web.wav        renata_micro.wav
 SING2.wav	  english_sxample.wav   renata_webwav.wav
 anton_mic.wav	  london_example.wav    rostelekom_example.wav
 antono_web.wav   misha1.wav	       'source (1).wav'
 dinara1.wav	  new_year.wav


In [16]:
from voice_conversion.export.inference_model import InferenceModel
from voice_conversion.wrapper import Wrapper
wrapper = Wrapper("english_voice_conversion_trimmed", "cuda:1",
                  "/mnt/tts/models/voice-conversion/VTTS-583-english-ablations/english_voice_conversion_trimmed/checkpoints/checkpoint-step=300000.ckpt")

[NeMo I 2022-10-18 11:27:28 cloud:56] Found existing object /root/.cache/torch/NeMo/NeMo_1.6.0rc0/stt_en_conformer_ctc_large/b2da9ca277cfb30bb0c6b2abd44eef02/stt_en_conformer_ctc_large.nemo.
[NeMo I 2022-10-18 11:27:28 cloud:62] Re-using file from: /root/.cache/torch/NeMo/NeMo_1.6.0rc0/stt_en_conformer_ctc_large/b2da9ca277cfb30bb0c6b2abd44eef02/stt_en_conformer_ctc_large.nemo
[NeMo I 2022-10-18 11:27:28 common:729] Instantiating model from pre-trained checkpoint
[NeMo I 2022-10-18 11:27:31 mixins:146] Tokenizer SentencePieceTokenizer initialized with 128 tokens


[NeMo W 2022-10-18 11:27:31 modelPT:135] If you intend to do training or fine-tuning, please call the ModelPT.setup_training_data() method and provide a valid configuration file to setup the train data loader.
    Train config : 
    manifest_filepath: /data/nemo_asr_set/asr_set_1.4/train_no_appen/tarred_audio_manifest.json
    sample_rate: 16000
    batch_size: 8
    shuffle: true
    num_workers: 8
    pin_memory: true
    use_start_end_token: false
    trim_silence: false
    max_duration: 20.0
    min_duration: 0.1
    shuffle_n: 2048
    is_tarred: true
    tarred_audio_filepaths: /data/nemo_asr_set/asr_set_1.4/train_no_appen/audio__OP_0..2047_CL_.tar
    
[NeMo W 2022-10-18 11:27:31 modelPT:142] If you intend to do validation, please call the ModelPT.setup_validation_data() or ModelPT.setup_multiple_validation_data() method and provide a valid configuration file to setup the validation data loader(s). 
    Validation config : 
    manifest_filepath:
    - /manifests/librispeech/l

[NeMo I 2022-10-18 11:27:31 features:264] PADDING: 0
[NeMo I 2022-10-18 11:27:31 features:281] STFT using torch
[NeMo I 2022-10-18 11:27:34 save_restore_connector:149] Model EncDecCTCModelBPE was successfully restored from /root/.cache/torch/NeMo/NeMo_1.6.0rc0/stt_en_conformer_ctc_large/b2da9ca277cfb30bb0c6b2abd44eef02/stt_en_conformer_ctc_large.nemo.


In [17]:
wrapper._inference_model(wav_source, mel_ref, pitch)

torch.Size([1, 256, 203]) torch.Size([1, 512, 203])


tensor([[[ 2.4923e-02,  2.0360e-02,  1.9590e-02,  ..., -8.3554e-05,
          -3.1092e-03, -2.2824e-03]]], device='cuda:1')